# **Weather type reconstruction with neural networks**

created by: Lucas Pfister, 2024

### ***Description:***

This notebook contains the code used for weather type reconstruction in Pfister et al. (2024). For details see the description in this paper. As the original station observations are not all publicly available (yet), a dummy dataset is available for demonstration purposes. The classification method is designed for 9 weather types (similar to the CAP9 classification (Weusthoff, 2011) used in the paper).


The notebook contains code to 1) read in 2) and preprocess the model input data, to 3) evaluate the model (independent validation) and to 4) create WT reconstructions. For this purpose, the numpy, pandas, matplotlib, tensorflow and sklearn libraries have to be installed.


## **0) Load libraries**

In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt

import tensorflow as tf
from tensorflow import keras

import sklearn
from sklearn.metrics import confusion_matrix
from sklearn.linear_model import LinearRegression
from sklearn.preprocessing import PolynomialFeatures

from sklearn.model_selection import train_test_split, KFold

2024-04-04 11:50:08.693263: I tensorflow/core/platform/cpu_feature_guard.cc:193] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.
2024-04-04 11:50:10.404215: W tensorflow/compiler/xla/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcudart.so.11.0'; dlerror: libcudart.so.11.0: cannot open shared object file: No such file or directory
2024-04-04 11:50:10.404275: I tensorflow/compiler/xla/stream_executor/cuda/cudart_stub.cc:29] Ignore above cudart dlerror if you do not have a GPU set up on your machine.
2024-04-04 11:50:15.358188: W tensorflow/compiler/xla/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libnvinfer.so.7'; dlerror: libnvinfer.so.7: cannot open shared object file: No such file or directory
2024-04-04

## **1) Read data**

For demonstration purposes, a dummy dataset is read with four pressure series (pp) and three temperature series (ta), as well as the weather types (WT) in the last column. Note that the dummy weather types (9 classes) losely match the patterns in the pressure and temperature series, so model training is possible.

In [3]:
## read dataset
training_data = pd.read_csv("WTrec_DummyTrainingData.csv", index_col=0)
training_data.index = pd.to_datetime(training_data.index)
training_data

AAA_pp  BBB_pp  CCC_pp  DDD_pp  EEE_pp  AAA_ta  BBB_ta  CCC_ta  WT
1957-09-01  1020.9  1013.9  1019.1  1012.4  1014.8    10.9    15.3    12.9   3
1957-09-02  1011.1  1009.1  1019.1  1004.4  1006.3    14.8    20.6    18.9   2
1957-09-03  1026.1  1015.7  1024.0  1020.1  1010.8    10.3    17.6    15.9   3
1957-09-04  1012.5  1024.6  1029.1  1021.3  1021.7    12.9    16.3    12.9   5
1957-09-05  1017.1  1016.7  1022.3  1012.2  1011.8     8.8    15.9    12.0   4
...            ...     ...     ...     ...     ...     ...     ...     ...  ..
2020-12-27  1006.9  1013.5  1020.0  1006.9  1015.0     4.2     5.4     5.7   2
2020-12-28  1010.2  1024.6  1029.3  1015.7  1019.4    -1.3     3.7     2.8   5
2020-12-29   989.5   989.4  1015.0   983.7   983.2     0.3     5.6     5.9   7
2020-12-30  1014.7  1005.9  1023.6  1012.0   998.3    -1.0     2.6     7.2   3
2020-12-31  1026.6  1020.1  1031.6  1029.2  1015.2    -4.6    -0.7    -7.5   5

[23133 rows x 9 columns]

In [4]:
## separate WT series from station data
WT_series = training_data.WT.copy()
data = training_data.drop("WT", axis=1)

## **2) Preprocessing**

Seasonality correction (fitting first two harmonics) and trend correction (3rd order polynomial) for temperature series. Standardization of model input data.

In [5]:
seascor = True # whether to correct temperature seasonality
detrend = True # whether to correct temperature trend

### **2.1) Seasonality correction**

In [6]:
def calcseas(t_series):
    '''Takes temperature series (Pandas Series object) and returns date array, fitted values (average seasonality) and residuals (anomalies from average seasonality)'''
    
    # get day of year and number of days
    doy = t_series.index.dayofyear
    ndoy = t_series.index.year.map(lambda x: pd.Timestamp(x, 12, 31).dayofyear)
    
    # array with 1st & 2nd harmonics (transposed)
    x = np.array([np.cos(2*np.pi*doy/ndoy),np.sin(2*np.pi*doy/ndoy),np.cos(4*np.pi*doy/ndoy),np.sin(4*np.pi*doy/ndoy)]).T

    # get temperature data
    y=t_series.values
    
    # get rid of na values for fit
    nonan_idx = np.where(~np.isnan(y))
    x_=x[nonan_idx]
    y_=y[nonan_idx]

    if y_.size == 0:
        print("observation vector is empty")
        ynew = res = np.zeros_like(y)*np.nan
        
    else:
        ## 2nd harmonics fit
        reg = LinearRegression().fit(x_, y_)
        
        # fitted values
        ynew = reg.predict(x)
        
        # residuals
        res = y-ynew
        
    return(t_series.index, ynew, res)

In [7]:
if seascor:
    print("apply seasonality correction")
    for x in data.filter(regex=r'ta').columns:
        print(x)
        tseries = data[x]
        t, n, r = calcseas(tseries)
        data[x] = r

apply seasonality correction
AAA_ta
BBB_ta
CCC_ta


### **2.2) Trend correction**

In [8]:
def detr_poly(t_series, poly_degree = 3):
    '''Takes temperature series (Pandas Series object) and returns detrended time series'''
    XX = np.reshape(t_series.index, (len(t_series.index), 1))
    YY = t_series
    pf = PolynomialFeatures(degree=poly_degree)
    Xp = pf.fit_transform(XX)
    md2 = LinearRegression()
    md2.fit(Xp, YY)
    trendp = md2.predict(Xp)
    
    series_detr = YY-trendp
    return series_detr

In [9]:
if detrend:
    print("detrend temperature data")
    for x in data.filter(regex=r'ta').columns:
        print(x)
        tseries = data[x]
        tseries_detr = detr_poly(tseries)
        data[x] = tseries_detr

detrend temperature data
AAA_ta
BBB_ta
CCC_ta


### **2.3) Standardization**

In [10]:
print("standardize data")
## normalize station data (column-wise)
statdata_norm = (data-data.mean())/data.std()

standardize data


In [11]:
statdata_norm

AAA_pp    BBB_pp    CCC_pp    DDD_pp    EEE_pp    AAA_ta  \
1957-09-01  0.861675 -0.118171  0.065897  0.280997  0.221356 -0.903708   
1957-09-02 -0.164191 -0.638198  0.065897 -0.582752 -0.584370  0.121121   
1957-09-03  1.406012  0.076840  0.693161  1.112355 -0.157809 -0.985966   
1957-09-04 -0.017639  1.041056  1.346027  1.241917  0.875417 -0.290144   
1957-09-05  0.463890  0.185178  0.475539  0.259403 -0.063018 -1.294703   
...              ...       ...       ...       ...       ...       ...   
2020-12-27 -0.603848 -0.161506  0.181109 -0.312831  0.240315  1.755074   
2020-12-28 -0.258403  1.041056  1.371630  0.637293  0.657397  0.377222   
2020-12-29 -2.425284 -2.772475 -0.458957 -2.817702 -2.774050  0.801216   
2020-12-30  0.212658 -0.984882  0.641955  0.237809 -1.342701  0.488447   
2020-12-31  1.458353  0.553531  1.666060  2.094869  0.259273 -0.408775   

              BBB_ta    CCC_ta  
1957-09-01 -1.544809 -0.721915  
1957-09-02  0.181912  0.918599  
1957-09-03 -0.735694  0.133359  
1957-09-04 -1.110568 -0.651333  
1957-09-05 -1.197688 -0.869345  
...              ...       ...  
2020-12-27  0.885801  0.834880  
2020-12-28  0.355913  0.064347  
2020-12-29  0.972339  0.910779  
2020-12-30  0.026072  1.271371  
2020-12-31 -1.016832 -2.682053  

[23133 rows x 8 columns]

## **3) Model tuning**

In [12]:
## define predictor and predictand data
dates = statdata_norm.index
x_data = statdata_norm.to_numpy()
y_data = WT_series.to_numpy()

n_data = x_data.shape[0]

y_data_1_hot = np.zeros((n_data, y_data.max()))
y_data_1_hot[np.arange(n_data),y_data-1] = 1

n_input = x_data.shape[1]
n_output = y_data_1_hot.shape[1]

### **3.1) Model setup**

As the time series in our dummy dataset correspond to the 1738 station set (5 pressure and 4 temperature series), either this model can be loaded or a new one can be created (un/comment corresponding lines)

In [13]:
### create NN model (from scratch)

#model = keras.Sequential()
    
## input layer
#model.add(tf.keras.layers.Input(name='input', dtype=tf.float32, shape=[n_input]))

## hidden layers
#model.add(tf.keras.layers.Dense(units=256, activation='relu'))
#model.add(tf.keras.layers.Dense(units=128, activation='relu'))
        
## dropout layer    
#model.add(tf.keras.layers.Dropout(rate = 0.1))
    
## output layer
#model.add(tf.keras.layers.Dense(units=n_output, name='output', activation='softmax'))

## compile model
#model.compile(optimizer=keras.optimizers.Adam(learning_rate=0.001), loss="categorical_crossentropy", metrics=['accuracy'])

#model.summary()

In [15]:
### read pre-trained model
model = tf.keras.models.load_model('NN_models/NN_hypermodel_stat_1738_tot.keras')
model.summary()

2024-04-04 11:50:52.023935: W tensorflow/compiler/xla/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcuda.so.1'; dlerror: libcuda.so.1: cannot open shared object file: No such file or directory
2024-04-04 11:50:52.025388: W tensorflow/compiler/xla/stream_executor/cuda/cuda_driver.cc:265] failed call to cuInit: UNKNOWN ERROR (303)
2024-04-04 11:50:52.025495: I tensorflow/compiler/xla/stream_executor/cuda/cuda_diagnostics.cc:156] kernel driver does not appear to be running on this host (climcal4.giub.unibe.ch): /proc/driver/nvidia/version does not exist
2024-04-04 11:50:52.027658: I tensorflow/core/platform/cpu_feature_guard.cc:193] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.


Model: "sequential"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 dense (Dense)               (None, 256)               2304      
                                                                 
 dense_1 (Dense)             (None, 128)               32896     
                                                                 
 dropout (Dropout)           (None, 128)               0         
                                                                 
 output (Dense)              (None, 9)                 1161      
                                                                 
Total params: 36,361
Trainable params: 36,361
Non-trainable params: 0
_________________________________________________________________


### **3.2) Model validation**

k-fold cross-validation. Note that this code is merely a regular cross-validation for a single model and not a nested cross-validation for hyperparameter tuning purposes.

In [16]:
## define input data
Xdata = x_data
ydata = y_data_1_hot

## define the K-fold cross validator
nfold_outer = 8
cv_outer = KFold(n_splits=nfold_outer, shuffle=False)#, random_state=42)

## define early stopping conditions for model tuning
stop_early = tf.keras.callbacks.EarlyStopping(monitor='val_loss', patience=5, mode="min")

## validation output table
accuracy_outer_post = pd.DataFrame(index=np.arange(1,nfold_outer+1), columns=["ANN","DJF","MAM","JJA","SON"])


## loop over folds
fold_outer = 1

for train, test in cv_outer.split(Xdata, ydata):
    print("outer_fold = "+str(fold_outer))
    print(train, test)
    
    ## define training and test data
    X_train = Xdata[train, :]
    y_train = ydata[train]
    dates_train = dates[train]
    
    X_test = Xdata[test, :]
    y_test = ydata[test]
    dates_test = dates[test]
    
    ## create model and tune it (with 1/7 of training data used for validation)
    NN_model = model
    NN_model.fit(X_train, y_train, validation_split=1/7, epochs=40, batch_size=200, callbacks=[stop_early])
        
    ## evaluate model
    y_pred = np.argmax(NN_model.predict(X_test), axis=1)+1
    y_tst = np.argmax(y_test, axis=1)+1
    
    ## overall accuracy
    acc_outer = sklearn.metrics.accuracy_score(y_tst, y_pred)
    accuracy_outer_post.loc[fold_outer, "ANN"] = acc_outer
    
    ## seasonal accuracy
    for i in [[12,1,2],[3,4,5],[6,7,8],[9,10,11]]:
        acc = sklearn.metrics.accuracy_score(y_tst[dates_test.month.isin(i)], y_pred[dates_test.month.isin(i)], normalize=True)
        if i == [12,1,2]:
            cc = "DJF"
        elif i == [3,4,5]:
            cc = "MAM"
        elif i == [6,7,8]:
            cc = "JJA"
        elif i == [9,10,11]:
            cc = "SON"
        accuracy_outer_post.loc[fold_outer, cc] = acc
    
    # Increase fold number
    fold_outer += 1

    

outer_fold = 1
[ 2892  2893  2894 ... 23130 23131 23132] [   0    1    2 ... 2889 2890 2891]
Epoch 1/40
87/87 [==============================] - 2s 13ms/step - loss: 0.6697 - accuracy: 0.7288 - val_loss: 0.6126 - val_accuracy: 0.7448
Epoch 2/40
87/87 [==============================] - 1s 10ms/step - loss: 0.5768 - accuracy: 0.7603 - val_loss: 0.5650 - val_accuracy: 0.7697
Epoch 3/40
87/87 [==============================] - 1s 10ms/step - loss: 0.5559 - accuracy: 0.7697 - val_loss: 0.5535 - val_accuracy: 0.7690
Epoch 4/40
87/87 [==============================] - 1s 10ms/step - loss: 0.5498 - accuracy: 0.7704 - val_loss: 0.5641 - val_accuracy: 0.7580
Epoch 5/40
87/87 [==============================] - 1s 10ms/step - loss: 0.5401 - accuracy: 0.7753 - val_loss: 0.5466 - val_accuracy: 0.7714
Epoch 6/40
87/87 [==============================] - 1s 10ms/step - loss: 0.5352 - accuracy: 0.7770 - val_loss: 0.5556 - val_accuracy: 0.7659
Epoch 7/40
87/87 [==============================] - 1s 10ms/s

In [17]:
## accuracy for all folds (overall and seasons)
accuracy_outer_post

ANN       DJF       MAM       JJA       SON
1  0.790111  0.785319  0.778533  0.827195  0.770604
2  0.784232  0.793629  0.802989  0.750708  0.788462
3   0.78769  0.783934  0.798913   0.78187  0.785714
4  0.785961  0.795014  0.789548   0.76703  0.792582
5   0.77213  0.808864  0.771955  0.722826  0.785714
6  0.781391  0.771468  0.791489  0.779891  0.782967
7  0.806987  0.832853  0.802183   0.79212  0.802198
8  0.767209  0.794501   0.73913  0.777174  0.759615

In [18]:
## average accuracy (overall and seasons)
print(accuracy_outer_post.mean(axis=0))

ANN    0.784464
DJF    0.795698
MAM    0.784343
JJA    0.774852
SON    0.783482
dtype: float64


## **4) Weather type reconstructions**

reconstruct WTs from our dummy station variables and evaluate the reconstructions.

In [19]:
## create predictions with pre-trained model (section 3)
preds = NN_model.predict(Xdata)
preds_class = np.argmax(preds, axis=1)+1
true_class = np.argmax(ydata, axis=1)+1

723/723 [==============================] - 2s 3ms/step


In [20]:
## create data frame with predicted and true WT time series
WT_rec = pd.DataFrame([preds_class, true_class], columns=dates, index=["predicted","true"]).T
WT_rec

predicted  true
1957-09-01          1     3
1957-09-02          2     2
1957-09-03          3     3
1957-09-04          5     5
1957-09-05          3     4
...               ...   ...
2020-12-27          1     2
2020-12-28          5     5
2020-12-29          7     7
2020-12-30          2     3
2020-12-31          5     5

[23133 rows x 2 columns]

In [21]:
## get overall accuracy
sklearn.metrics.accuracy_score(WT_rec.true, WT_rec.predicted)

0.8026196342886786

In [22]:
## confusion matrix
confmat = sklearn.metrics.confusion_matrix(WT_rec.true, WT_rec.predicted,  labels = [1, 2, 3, 4, 5, 6, 7, 8, 9], normalize = "true")
df = pd.DataFrame(confmat)*100
df.index = df.columns = [1,2,3,4,5,6,7,8,9]
df.style.background_gradient(cmap ='Blues').set_properties(**{'font-size': '20px'})